In [1]:
import math
import argparse
import sys
import numpy as np

import torch
from torch import nn
import torch.nn.functional as F
from torch.nn.parameter import Parameter
import torch.optim as optim
from torchvision import datasets, transforms
from torch.autograd import Variable, Function

## Define Module

In [2]:
class GenWeights(Function):
    def __init__(self, ops, in_channels, out_channels, kernel_size, groups=1):
        self.ops = ops
        self.in_channels = in_channels
        self.out_channels = out_channels
        self.kernel_size = kernel_size
        self.groups = groups
        self.ncoeff = list(self.ops.size())[-1]
        
    def forward(self, coeffs):
        w = torch.sum(torch.mul(coeffs.view(self.out_channels, self.in_channels, 1, 1, self.ncoeff), self.ops), 
                      dim=-1)
        weight = Variable(w, requires_grad=False)
        return weight

    def backward(self, weight_grad):
        return torch.mul(weight_grad.unsqueeze(-1), self.ops).sum(2).sum(2)

class FdConv2d(nn.Module):
    def __init__(self, in_channels, out_channels, degree=2, stride=1, padding=0, dilation=1, groups=1, bias=True):
        assert degree in [0,1,2]
        super(FdConv2d, self).__init__()
        if in_channels % groups != 0:
            raise ValueError('in_channels must be divisible by groups')
        if out_channels % groups != 0:
            raise ValueError('out_channels must be divisible by groups')
        self.in_channels = in_channels
        self.out_channels = out_channels
        self.degree = degree
        self.kernel_size = (3, 3)
        self.stride = stride
        self.padding = padding
        self.dilation = dilation
        self.groups = groups
        if bias:
            self.bias = Parameter(torch.Tensor(out_channels))
        else:
            self.register_parameter('bias', None)
#         self.ncoeff = int((self.degree + 1) * (self.degree + 2) / 2)
        self.ncoeff = 9
        self.coeffs = torch.Tensor(out_channels, in_channels // groups, self.ncoeff)
        if torch.cuda.is_available():
            self.coeffs = self.coeffs.cuda()
        self.coeffs = Parameter(self.coeffs)
        self.set_weights()
        
    def set_weights(self):
        n = self.in_channels * self.ncoeff
        stdv = 1. / math.sqrt(n)
        self.coeffs.data.uniform_(-stdv, stdv)
        ops = self.get_diff_operators()
        self.weight = GenWeights(ops, self.in_channels, self.out_channels, self.kernel_size)(self.coeffs)
            
    def get_diff_operators(self):
        operators = []
#         # add degree zero
#         operators.append([[0,0,0],[0,1,0],[0,0,0]])
#         # add degree one
#         if self.degree > 0:
#             operators.append([[0,0,0],[-1,0,1],[0,0,0]])
#             operators.append([[0,1,0],[0,0,0],[0,-1,0]])
#         # add degree two
#         if self.degree > 1:
#             operators.append([[-.25,0,.25],[0,0,0],[.25,0,-.25]])
#             operators.append([[0,0,0],[1,-2,1],[0,0,0]])
#             operators.append([[0,1,0],[0,-2,0],[0,1,0]])
        operators.append([[1,0,0],[0,0,0],[0,0,0]])
        operators.append([[0,1,0],[0,0,0],[0,0,0]])
        operators.append([[0,0,1],[0,0,0],[0,0,0]])
        operators.append([[0,0,0],[1,0,0],[0,0,0]])
        operators.append([[0,0,0],[0,1,0],[0,0,0]])
        operators.append([[0,0,0],[0,0,1],[0,0,0]])
        operators.append([[0,0,0],[0,0,0],[1,0,0]])
        operators.append([[0,0,0],[0,0,0],[0,1,0]])
        operators.append([[0,0,0],[0,0,0],[0,0,1]])
        ops = torch.tensor(operators, dtype=torch.float)
        ops = ops.permute(1, 2, 0)  # shape (3, 3, ncoeff)
        if torch.cuda.is_available():
            ops = ops.cuda()
        return ops
        
    def forward(self, input):
        return F.conv2d(input, self.weight, self.bias, self.stride,
                        self.padding, self.dilation, self.groups)

## Define Model

In [3]:
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.csize = 20*7*7
#         self.conv1 = nn.Conv2d(1, 10, kernel_size=5)
#         self.conv2 = nn.Conv2d(10, 20, kernel_size=5)
#         self.conv1 = nn.Conv2d(1, 10, kernel_size=3, padding=1)
#         self.conv2 = nn.Conv2d(10, 20, kernel_size=3, padding=1)
        self.conv1 = FdConv2d(1, 10, degree=2, padding=1)
        self.conv2 = FdConv2d(10, 20, degree=2, padding=1)
        self.conv2_drop = nn.Dropout2d()
        self.fc1 = nn.Linear(self.csize, 50)
        self.fc2 = nn.Linear(50, 10)

    def forward(self, x):
        x = F.relu(F.max_pool2d(self.conv1(x), 2))
        x = F.relu(F.max_pool2d(self.conv2_drop(self.conv2(x)), 2))
        x = x.view(-1, self.csize)
        x = F.relu(self.fc1(x))
        x = F.dropout(x, training=self.training)
        x = self.fc2(x)
        return F.log_softmax(x, dim=1)

## Train and Test

In [4]:
def train(args, model, device, train_loader, optimizer, epoch):
    model.train()
    for batch_idx, (data, target) in enumerate(train_loader):
        data, target = data.to(device), target.to(device)
        optimizer.zero_grad()
        output = model(data)
        loss = F.nll_loss(output, target)
        loss.backward()
        print(model.conv1.coeffs.grad)
        print(model.conv1.coeffs)
#         print(model.conv1.weight.grad)
#         print(model.conv1.weight)
#         import ipdb; ipdb.set_trace()
        optimizer.step()
        print(model.conv1.coeffs)
#         print(model.conv1.coeffs)
        if batch_idx % args.log_interval == 0:
            sys.stdout.write('Train Epoch: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f} \r'.format(
                epoch, batch_idx * len(data), len(train_loader.dataset),
                100. * batch_idx / len(train_loader), loss.item()))
            sys.stdout.flush()

def test(args, model, device, test_loader):
    model.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        for data, target in test_loader:
            data, target = data.to(device), target.to(device)
            output = model(data)
            test_loss += F.nll_loss(output, target, size_average=False).item() # sum up batch loss
            pred = output.max(1, keepdim=True)[1] # get the index of the max log-probability
            correct += pred.eq(target.view_as(pred)).sum().item()

    test_loss /= len(test_loader.dataset)
    print('\nTest set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%) \r'.format(
        test_loss, correct, len(test_loader.dataset),
        100. * correct / len(test_loader.dataset)))

## Run

In [5]:
# Training settings
parser = argparse.ArgumentParser(description='PyTorch MNIST Example')
parser.add_argument('--batch-size', type=int, default=64, metavar='N',
                    help='input batch size for training (default: 64)')
parser.add_argument('--test-batch-size', type=int, default=1000, metavar='N',
                    help='input batch size for testing (default: 1000)')
parser.add_argument('--epochs', type=int, default=100, metavar='N',
                    help='number of epochs to train (default: 10)')
parser.add_argument('--lr', type=float, default=1e-2, metavar='LR',
                    help='learning rate (default: 0.01)')
parser.add_argument('--momentum', type=float, default=0.5, metavar='M',
                    help='SGD momentum (default: 0.5)')
parser.add_argument('--no-cuda', action='store_true', default=False,
                    help='disables CUDA training')
parser.add_argument('--seed', type=int, default=1, metavar='S',
                    help='random seed (default: 1)')
parser.add_argument('--log-interval', type=int, default=10, metavar='N',
                    help='how many batches to wait before logging training status')
args = parser.parse_args('')
use_cuda = not args.no_cuda and torch.cuda.is_available()

torch.manual_seed(args.seed)

device = torch.device("cuda" if use_cuda else "cpu")

kwargs = {'num_workers': 1, 'pin_memory': True} if use_cuda else {}
train_loader = torch.utils.data.DataLoader(
    datasets.MNIST('../data', train=True, download=True,
                   transform=transforms.Compose([
                       transforms.ToTensor(),
                       transforms.Normalize((0.1307,), (0.3081,))
                   ])),
    batch_size=args.batch_size, shuffle=True, **kwargs)
test_loader = torch.utils.data.DataLoader(
    datasets.MNIST('../data', train=False, transform=transforms.Compose([
                       transforms.ToTensor(),
                       transforms.Normalize((0.1307,), (0.3081,))
                   ])),
    batch_size=args.test_batch_size, shuffle=True, **kwargs)

model = Net().to(device)
optimizer = optim.SGD(model.parameters(), lr=args.lr, momentum=args.momentum)
# optimizer = optim.Adam(model.parameters(), lr=args.lr)

for epoch in range(1, args.epochs + 1):
    train(args, model, device, train_loader, optimizer, epoch)
    test(args, model, device, test_loader)

tensor(1.00000e-02 *
       [[[ 0.0609,  0.0322,  0.3694,  0.8974,  1.0944,  0.7671,  1.5596,
           1.7870,  1.6816]],

        [[ 0.7333,  0.0585, -0.0713,  0.4912,  0.0027, -0.8105,  0.5227,
          -0.1166, -0.5016]],

        [[-0.4667, -0.3331,  0.3180, -0.3812, -0.6049,  0.3084, -0.0430,
          -0.8976,  0.0380]],

        [[-0.3208, -0.3563, -0.8801,  0.6719,  0.4695, -0.3575,  1.1839,
           0.3019, -0.4351]],

        [[ 0.4800,  0.0793,  0.3297,  0.9705,  0.6308,  0.3034,  1.2588,
           0.5478, -0.3747]],

        [[-0.2257, -0.0542,  0.2626, -0.2594, -0.2943, -0.1421,  0.1678,
           0.1902,  0.2060]],

        [[-0.3661, -0.0848, -0.0425, -0.2179,  0.4642,  0.3335,  0.1980,
          -0.2377, -0.5799]],

        [[ 0.2996,  0.5127, -0.3784,  0.5083,  0.5616, -0.2972,  1.2968,
           0.3541, -0.2588]],

        [[ 0.0852,  0.3449,  0.2729,  0.2228,  0.4130,  0.3697,  0.4258,
           0.3366,  0.4260]],

        [[-0.2652, -0.0289,  0.0762, -0.275

tensor(1.00000e-02 *
       [[[ 0.3493, -0.6138, -0.9627,  0.1185, -1.2572, -1.2451, -0.3037,
          -1.5406, -1.3186]],

        [[-1.0403, -0.6673, -0.1783, -0.5563,  0.0456, -0.0007, -0.3646,
           0.0359,  0.0704]],

        [[ 0.2794,  0.0429, -0.0692,  1.1120,  0.9156,  0.5594,  1.3648,
           1.1324,  0.7539]],

        [[ 0.2422,  0.1128,  0.0261, -0.0963, -0.2312,  0.6449, -0.3571,
          -0.1810, -0.0068]],

        [[ 0.2980,  0.1799,  0.1311, -0.4210, -0.8138, -0.7010, -0.1581,
          -1.3717, -1.3148]],

        [[ 0.6021,  0.2496, -0.4032,  0.2844, -0.5044, -0.4367, -0.6400,
          -0.8953, -0.5607]],

        [[-0.3336, -0.0367,  0.3617, -0.5962,  0.2804,  0.1574, -0.1957,
           0.5046,  0.2233]],

        [[-0.7382, -1.4031, -0.9844,  0.0125, -0.8304, -0.2796, -0.0758,
          -0.2308, -0.0265]],

        [[-0.3158, -0.0110,  0.1345,  0.0688,  0.0434,  0.0772, -0.1134,
          -0.1695, -0.0469]],

        [[-0.7824, -0.1873, -0.4312, -0.929

tensor(1.00000e-02 *
       [[[-0.8740, -1.4225, -1.4329, -1.2653, -1.6246, -1.5192, -1.1816,
          -0.9655, -0.6448]],

        [[-1.1045, -0.1912, -0.0711, -0.2898,  0.0567, -0.0650, -1.0017,
          -0.5795, -0.5642]],

        [[-1.8718, -1.4325, -1.0495, -0.7505, -1.0339, -0.8379,  0.1463,
          -0.3058, -0.7906]],

        [[-1.9900, -2.0791, -1.1557, -0.9428, -1.5500, -1.0384, -1.0090,
          -1.3462, -1.0281]],

        [[-1.0843, -0.6454,  0.0783, -0.8068, -1.5310, -0.5725, -1.1994,
          -1.6250, -0.4413]],

        [[ 1.2406,  0.4173, -0.6230,  0.5414, -0.0920, -0.4198,  0.4092,
          -0.2782, -0.1298]],

        [[-0.3289,  0.1702, -0.1447, -0.0050,  0.4337, -0.4219,  0.4142,
           0.2300, -0.3859]],

        [[-0.3388, -0.1769, -0.5513, -0.2716,  0.0191, -0.2889, -0.8665,
          -0.2727, -0.2559]],

        [[ 0.3334,  0.4116, -0.1895,  0.3721,  0.4937,  0.0504,  0.1609,
           0.4074,  0.0296]],

        [[-0.6703, -0.2194,  0.1846, -1.654

tensor(1.00000e-02 *
       [[[ 0.1668,  0.5086,  0.7490,  0.8159,  0.3780, -0.0804,  0.2428,
          -0.1842, -0.3515]],

        [[-0.3839,  0.0724,  0.1618,  0.1423,  0.3019,  0.3853,  0.5527,
           0.6914,  0.6046]],

        [[ 0.3455,  1.5561,  1.5249,  0.4614,  1.3463,  0.7158,  0.1132,
           0.6605,  0.5390]],

        [[-2.1253, -2.6409, -1.9202, -2.0266, -2.4076, -1.6413, -0.2462,
          -1.1526, -0.7329]],

        [[-0.9035, -0.1324,  0.0768, -0.2650, -0.2500,  0.2408, -0.3280,
          -0.8128,  0.0980]],

        [[ 0.1437, -0.0595,  0.0856, -0.4105, -0.1838,  0.6309,  0.2840,
           0.1968,  0.2685]],

        [[ 0.2756,  0.2536,  0.3818, -0.2771, -0.4288, -0.3847, -0.1931,
          -0.4634, -0.3712]],

        [[-1.1549, -1.1422,  0.0956, -1.5856, -0.6367,  0.4075, -1.1735,
           0.0660,  0.8041]],

        [[-0.4155, -0.4731, -0.8573, -0.7043, -0.5195, -0.6722, -0.5016,
          -0.4219, -0.5234]],

        [[-1.3494, -0.9008, -0.0356, -1.939

tensor(1.00000e-02 *
       [[[-0.7853, -0.4257, -0.0236,  0.3188, -0.0159,  0.2244,  1.4067,
           1.2314,  1.0897]],

        [[-0.7269, -0.2884, -0.2235,  0.2259,  0.0975, -0.4652,  1.1835,
           0.9223,  0.1430]],

        [[-2.3622, -2.0702, -1.1400, -1.4828, -1.0409, -0.7839, -0.1211,
          -0.1914, -0.0193]],

        [[-1.9725, -1.9368, -1.0954, -2.6944, -1.8160, -1.3216, -2.0068,
          -2.7616, -1.8538]],

        [[-0.5735, -0.5060, -0.3455, -1.2397, -1.5643, -1.5164, -1.3337,
          -2.0984, -1.5243]],

        [[ 0.9678,  1.4235,  1.2097,  0.2841,  0.5257,  0.4955, -0.0715,
          -0.2482,  0.0804]],

        [[ 0.1212, -0.5329, -0.4088,  0.3001, -0.1289, -0.6890,  0.1128,
           0.1090, -0.5408]],

        [[-1.5114, -0.9315, -0.4872, -1.3216, -0.9048, -0.5197, -0.8906,
          -0.1789,  0.0045]],

        [[-0.2049, -0.5362, -1.4492, -0.0004, -0.2430, -1.3032,  0.0162,
          -0.1369, -1.0720]],

        [[-2.0191, -2.0731, -1.0204, -3.387

...

Parameter containing:
tensor([[[ 0.3487,  0.8086,  1.5859,  0.6585,  2.1396,  2.4144,  1.1527,
           2.0836,  2.0444]],

        [[ 0.7856,  0.2006,  0.0332,  0.0119,  0.1070, -0.4606, -0.3171,
          -0.7548, -1.0772]],

        [[ 0.6708, -0.0379,  0.6177,  0.5983,  1.4364,  1.1233,  1.1300,
           1.6735,  1.6186]],

        [[ 2.8599,  3.5504,  2.5085,  2.9600,  3.3051,  1.8702,  2.6063,
           2.4004,  0.9892]],

        [[ 1.0772,  1.1416,  1.0728,  1.2965,  1.6122,  1.2689,  0.4403,
           1.6647,  1.1433]],

        [[-0.4287, -0.3467, -0.3228, -0.5002, -0.3392, -0.1199, -0.3872,
          -0.0823, -0.2972]],

        [[ 0.7416,  1.0959,  1.7988, -0.2629,  0.2951,  0.6621, -0.7717,
          -0.2706,  0.5243]],

        [[ 0.6334,  0.1299, -0.4941,  1.1855,  0.2929, -0.2978,  0.8404,
           0.0519, -0.1337]],

        [[ 0.2444,  0.4473,  1.0198,  0.4483,  0.6803,  1.1994, -0.2208,
          -0.1941,  0.2334]],

        [[ 1.5534,  1.2855,  0.5271,  2.48

Parameter containing:
tensor([[[ 0.3488,  0.8088,  1.5866,  0.6591,  2.1412,  2.4162,  1.1539,
           2.0855,  2.0459]],

        [[ 0.7867,  0.2004,  0.0330,  0.0121,  0.1064, -0.4611, -0.3185,
          -0.7570, -1.0792]],

        [[ 0.6710, -0.0377,  0.6187,  0.5997,  1.4382,  1.1259,  1.1322,
           1.6761,  1.6212]],

        [[ 2.8629,  3.5555,  2.5130,  2.9634,  3.3099,  1.8748,  2.6085,
           2.4038,  0.9918]],

        [[ 1.0796,  1.1439,  1.0745,  1.2992,  1.6150,  1.2716,  0.4418,
           1.6665,  1.1448]],

        [[-0.4294, -0.3468, -0.3226, -0.5019, -0.3394, -0.1202, -0.3886,
          -0.0823, -0.2974]],

        [[ 0.7429,  1.0989,  1.8020, -0.2630,  0.2963,  0.6632, -0.7726,
          -0.2704,  0.5245]],

        [[ 0.6321,  0.1290, -0.4947,  1.1860,  0.2925, -0.2977,  0.8397,
           0.0516, -0.1330]],

        [[ 0.2457,  0.4490,  1.0220,  0.4492,  0.6818,  1.2014, -0.2207,
          -0.1937,  0.2344]],

        [[ 1.5540,  1.2867,  0.5269,  2.48

tensor(1.00000e-02 *
       [[[ 0.2937,  0.3114, -0.6326, -0.5498, -3.4884, -4.4199, -0.4670,
          -1.6598, -2.4386]],

        [[-0.7265,  0.2356, -0.0658, -3.4257, -2.0108,  0.0301, -4.0018,
          -1.9654,  1.1373]],

        [[ 0.2915,  0.5459, -0.4268, -2.7983, -1.5607, -3.1435, -4.7382,
          -3.9921, -2.6666]],

        [[-5.1507, -6.4668, -3.8088, -2.6336, -3.0819, -1.6326, -0.8047,
          -1.1218, -2.0529]],

        [[-1.7115, -4.0632, -5.0280, -4.4440, -5.8130, -4.4715, -3.0897,
          -3.5673, -3.4953]],

        [[ 1.4740, -0.9716, -3.1604,  0.9807, -1.5550, -2.2628,  1.2115,
          -0.8728, -0.5280]],

        [[ 1.8354,  0.0180,  0.4296,  2.6618,  0.3669,  1.8801,  3.9862,
           3.3013,  2.6616]],

        [[-2.2774, -1.2584,  1.9375, -1.9819,  0.9602,  2.9066, -3.8289,
          -2.5840, -0.0435]],

        [[-0.1540, -0.3461, -1.1469, -0.8772, -1.2580, -2.0020,  0.6581,
           0.8396, -0.2355]],

        [[-5.5134, -9.4419, -8.8023, -5.014

Process Process-3:
Traceback (most recent call last):
  File "/usr/lib/python3.5/multiprocessing/process.py", line 249, in _bootstrap
    self.run()
  File "/usr/lib/python3.5/multiprocessing/process.py", line 93, in run
    self._target(*self._args, **self._kwargs)
  File "/usr/local/lib/python3.5/dist-packages/torch/utils/data/dataloader.py", line 57, in _worker_loop
    samples = collate_fn([dataset[i] for i in batch_indices])
  File "/usr/local/lib/python3.5/dist-packages/torch/utils/data/dataloader.py", line 57, in <listcomp>
    samples = collate_fn([dataset[i] for i in batch_indices])
  File "/usr/local/lib/python3.5/dist-packages/torchvision/datasets/mnist.py", line 77, in __getitem__
    img = self.transform(img)
  File "/usr/local/lib/python3.5/dist-packages/torchvision/transforms/transforms.py", line 49, in __call__
    img = t(img)
  File "/usr/local/lib/python3.5/dist-packages/torchvision/transforms/transforms.py", line 143, in __call__
    return F.normalize(tensor, self.

KeyboardInterrupt: 

In [ ]:
params = dict(model.named_parameters())

In [ ]:
for k in params.keys():
    print(k, "shape: ", params[k].device)
#     print(params[k])

In [ ]:
print(optimizer)

In [ ]:
import torch
from torch.autograd import Variable
import torch.nn as nn

class MyFun(torch.autograd.Function):
    def __init__(self, a="hello\n"):
        self.a = a
        
    def forward(self, inp):
        print(self.a)
        return inp

    def backward(self, grad_out):
        grad_input = grad_out.clone()
        print('Custom backward called!')
        return grad_input
    
class MyMod(nn.Module):
    def forward(self, x):
        return MyFun(a="This is Max!\n")(x)

mod = MyMod()

y = Variable(torch.randn(1), requires_grad=True)
z = mod(y)
z.backward()

In [ ]:
f = MyFun()
print(f)